In [1]:
#Part1 定义模型
import torch
torch.manual_seed(0) #固定随机数种子，确保参数（训练效果）一致
torch.backends.cudnn.deterministic = False #GPU使用默认算法
torch.backends.cudnn.benchmark = True #GPU寻找最优算法

import torchvision.models as models
import torchvision.transforms as transforms
import torchvision.datasets as datasets
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torch.autograd import Variable
from torch.utils.data.dataset import Dataset

from ctypes.wintypes import INT, LONG
import os, sys, glob, shutil, json
from pickletools import long1, long4
import cv2

from PIL import Image
import numpy as np
from torch.utils.data.dataset import Dataset


# 定义模型
class SVHN_Model1(nn.Module): #输入数据为3x64x128
    def __init__(self):
        super(SVHN_Model1, self).__init__() #super()可以理解为指向父类的指针
        # CNN提取特征模块
        self.cnn = nn.Sequential( #顺序构建网络
            nn.Conv2d(3, 16, kernel_size=(3, 3), stride=(2, 2)), #in_channel, out_channel, 卷积核大小, 滑动步长
            nn.ReLU(),  #非线性激活函数，为了避免神经网络中全部是线性函数，那样就不需要神经网络了
            nn.MaxPool2d(2), #最大池化MaxPooling，大小为2x2
            nn.Conv2d(16, 32, kernel_size=(3, 3), stride=(2, 2)),
            nn.ReLU(), 
            nn.MaxPool2d(2),
        )
        # 
        self.fc1 = nn.Linear(32*3*7, 11)
        self.fc2 = nn.Linear(32*3*7, 11) #有点问题
        self.fc3 = nn.Linear(32*3*7, 11)
        self.fc4 = nn.Linear(32*3*7, 11)
        self.fc5 = nn.Linear(32*3*7, 11)
        self.fc6 = nn.Linear(32*3*7, 11)
    
    def forward(self, img):
        feat = self.cnn(img)
        feat = feat.view(feat.shape[0], -1)
        c1 = self.fc1(feat)
        c2 = self.fc2(feat)
        c3 = self.fc3(feat)
        c4 = self.fc4(feat)
        c5 = self.fc5(feat)
        c6 = self.fc6(feat)
        return c1, c2, c3, c4, c5, c6
    

model = SVHN_Model1()

In [2]:
#Part2 读取模型
model.load_state_dict(torch.load('./model.pt'))

<All keys matched successfully>

In [13]:
#Part3 模型测试
import pandas as pd
#from torchvision.transforms import ToTensor
#from torchvision.transforms import Resize

predict = []
test_glob = glob.glob('C:/Project/python/Jupyter/Practise/tianchi/data/mchar_test_a/mchar_test_a/*.png') #批量读取文件名到列表
for test_path in test_glob:
    img = Image.open(test_path).convert('RGB')
    img=img.resize((64,128))
        
    totensor = transforms.ToTensor()  #将PIL image或ndarray类型变换成tensor形式
    tensor0 = totensor(img)
    print(tensor0.shape)
    
    torch_norm = transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
    tensor0 = torch_norm(tensor0)

    tensor0 = Variable(torch.unsqueeze(tensor0, dim=0).float(), requires_grad=False)
    print(tensor0.shape)  #[1,3, 224, 224]

    
    
    '''
    size = transforms.Resize((64, 128)), #固定尺寸
    
    totensor = ToTensor()  #将PIL image或ndarray类型变换成tensor形式
    
    
    tensor_type = totensor(size(img))
    需要查一下参数表，看看totensor，Resize的参量，normalize的用法和参量
    '''
    
    c0, c1, c2, c3, c4, c5 = model(tensor0)
    pre = [c0, c1, c2, c3, c4, c5]
    print(pre)
    #pre.remove(10) #根据值删除元素
    predict.append(pre)
df = pd.DataFrame(predict)
df.to_excel("./predict.xls")

torch.Size([3, 128, 64])
torch.Size([1, 3, 128, 64])
[tensor([[-20.3659, -10.3961, -19.4860, -21.3772, -20.8707, -22.0117, -17.1156,
         -19.6775, -22.8039, -24.1549, -78.7592]], grad_fn=<AddmmBackward0>), tensor([[-16.0083, -17.5165, -15.1448, -19.3909, -14.5471, -20.0822, -20.3792,
         -23.3873, -17.8293, -16.3769, -22.7081]], grad_fn=<AddmmBackward0>), tensor([[-30.4470, -29.4899, -25.6738, -30.5617, -27.9147, -32.6160, -32.8748,
         -36.5105, -28.7857, -24.2568, -36.5968]], grad_fn=<AddmmBackward0>), tensor([[-61.6439, -61.5796, -58.6707, -59.5183, -58.4173, -56.5339, -59.8778,
         -73.4433, -61.7890, -63.2968, -66.7216]], grad_fn=<AddmmBackward0>), tensor([[-132.1227, -166.8265, -101.7430, -217.7343, -101.5852, -184.7625,
         -101.7392, -154.1939, -101.7886, -152.2721,  -66.7843]],
       grad_fn=<AddmmBackward0>), tensor([[-58.7148, -59.2801, -60.5677, -59.8357, -60.2761, -60.1878, -59.8382,
         -60.7565, -87.6858, -60.0776,  78.4234]], grad_fn=<Addm

torch.Size([1, 3, 128, 64])
[tensor([[-11.3353,  -3.8681,  -7.5659, -10.4980,  -6.4465, -10.7925,  -6.4832,
         -10.8452,  -5.6664,  -8.2126, -37.9872]], grad_fn=<AddmmBackward0>), tensor([[-5.4756, -4.8344, -7.0462, -8.6588, -5.8598, -9.2297, -7.7036, -9.1492,
         -7.8088, -6.5923, -6.8517]], grad_fn=<AddmmBackward0>), tensor([[-12.1300, -11.3633, -13.9579, -11.4180, -10.9510, -12.2900, -14.4364,
         -13.5792, -12.6514, -10.5110, -12.3540]], grad_fn=<AddmmBackward0>), tensor([[-23.9141, -26.9077, -24.9098, -24.0253, -24.7003, -22.3651, -25.5939,
         -28.2077, -23.1875, -24.2527, -24.0085]], grad_fn=<AddmmBackward0>), tensor([[-60.3930, -61.6205, -49.0820, -85.7702, -49.1939, -75.7268, -49.1022,
         -56.3827, -49.0764, -72.3601, -27.8429]], grad_fn=<AddmmBackward0>), tensor([[-29.2842, -29.4523, -29.8643, -29.7172, -29.8925, -29.9055, -29.6933,
         -29.9824, -36.8250, -29.8342,  31.9869]], grad_fn=<AddmmBackward0>)]
torch.Size([3, 128, 64])
torch.Size([1, 

torch.Size([1, 3, 128, 64])
[tensor([[-18.9906,  -6.7039,  -8.2665, -10.4600, -11.3624, -12.1339, -12.3264,
         -10.4253,  -8.1147, -11.9492, -50.1273]], grad_fn=<AddmmBackward0>), tensor([[ -9.1628,  -8.3262,  -6.3844,  -9.0717,  -9.0626, -13.7329, -14.9854,
          -7.8389, -10.9338,  -7.4372,  -9.3535]], grad_fn=<AddmmBackward0>), tensor([[-15.7248, -16.0199, -14.6692, -17.7275, -14.4450, -20.9662, -18.7717,
         -14.1784, -16.9153, -19.2521, -16.1257]], grad_fn=<AddmmBackward0>), tensor([[-32.4528, -39.2892, -32.1332, -36.2899, -31.1314, -41.6383, -33.8822,
         -34.1277, -35.6969, -40.5580, -31.1630]], grad_fn=<AddmmBackward0>), tensor([[ -93.1138,  -91.2221,  -62.1485, -116.9912,  -62.2616, -104.0828,
          -62.1266,  -62.3923,  -62.1278, -106.7179,  -33.5618]],
       grad_fn=<AddmmBackward0>), tensor([[-37.5025, -38.2295, -38.7378, -38.4435, -38.5156, -38.7453, -38.3779,
         -38.7208, -50.5034, -38.5928,  46.3997]], grad_fn=<AddmmBackward0>)]
torch.Size(

torch.Size([3, 128, 64])
torch.Size([1, 3, 128, 64])
[tensor([[-10.0414,  -2.4469,  -4.0234,  -3.3334,  -6.1620,  -4.9376,  -5.0994,
          -3.8114,  -3.9001,  -4.9997, -33.4124]], grad_fn=<AddmmBackward0>), tensor([[-4.2477, -5.3171, -4.6119, -4.0413, -5.5296, -5.3023, -5.8485, -3.9764,
         -4.2026, -3.0710, -1.7873]], grad_fn=<AddmmBackward0>), tensor([[-9.1199, -8.2638, -8.2237, -7.8393, -7.4041, -8.5480, -9.5513, -8.0256,
         -8.1146, -8.3389, -4.8103]], grad_fn=<AddmmBackward0>), tensor([[-17.2688, -18.7977, -17.8408, -19.0665, -21.3192, -21.6663, -20.4044,
         -21.6052, -19.4317, -19.4022, -11.8543]], grad_fn=<AddmmBackward0>), tensor([[-62.7439, -56.4594, -39.5733, -48.0971, -39.6914, -62.7361, -39.5670,
         -46.9341, -39.6293, -59.9552, -14.8451]], grad_fn=<AddmmBackward0>), tensor([[-25.7090, -25.5477, -25.9615, -25.6858, -25.7947, -25.8548, -25.6450,
         -25.8266, -34.9325, -25.7046,  32.6363]], grad_fn=<AddmmBackward0>)]
torch.Size([3, 128, 64])
t

torch.Size([1, 3, 128, 64])
[tensor([[-11.0041,  -3.9799,  -7.1336, -10.5428,  -6.9521, -11.6609,  -7.9405,
          -6.9257,  -9.3594,  -9.9742, -44.6823]], grad_fn=<AddmmBackward0>), tensor([[ -4.5771,  -5.4901,  -6.5946,  -8.5439,  -6.1468,  -9.9626,  -8.2902,
          -7.5778,  -8.7664,  -7.1592, -10.7718]], grad_fn=<AddmmBackward0>), tensor([[-13.5049, -12.2255, -12.9960, -13.2553, -11.3342, -14.4365, -13.3657,
         -13.2348, -13.3703, -12.5969, -12.7287]], grad_fn=<AddmmBackward0>), tensor([[-27.3028, -29.0678, -26.5928, -28.2928, -27.2303, -29.8195, -27.9632,
         -30.0208, -27.8148, -27.9800, -23.9964]], grad_fn=<AddmmBackward0>), tensor([[-72.3560, -70.1810, -56.7735, -99.5067, -56.7984, -91.7277, -56.8594,
         -60.4191, -56.7859, -89.6843, -31.0935]], grad_fn=<AddmmBackward0>), tensor([[-33.6606, -34.0469, -34.4928, -34.3514, -34.3773, -34.4368, -34.2983,
         -34.5774, -46.8500, -34.3880,  40.7296]], grad_fn=<AddmmBackward0>)]
torch.Size([3, 128, 64])
torc

...

torch.Size([1, 3, 128, 64])
[tensor([[-10.3957,  -2.4873,  -6.4118,  -7.7906,  -7.1504,  -8.1799,  -6.6957,
          -5.6487,  -7.8134,  -7.8406, -35.7829]], grad_fn=<AddmmBackward0>), tensor([[-4.1804, -5.2707, -5.5333, -6.6286, -6.4809, -7.7619, -7.1195, -5.9930,
         -6.7693, -5.8629, -6.8607]], grad_fn=<AddmmBackward0>), tensor([[-10.7545,  -9.8646, -10.6859, -11.9699, -10.7225, -12.3374, -10.8799,
         -11.0150, -11.2529, -11.0121,  -9.7859]], grad_fn=<AddmmBackward0>), tensor([[-21.1295, -23.4989, -23.5625, -24.4000, -22.2118, -23.8322, -25.2413,
         -22.6893, -23.3502, -22.0298, -18.1969]], grad_fn=<AddmmBackward0>), tensor([[-62.4523, -66.5172, -44.6953, -69.5074, -44.6525, -78.9957, -44.6255,
         -53.1131, -44.6103, -64.9244, -16.0216]], grad_fn=<AddmmBackward0>), tensor([[-27.3501, -27.7444, -28.0336, -27.8269, -27.9794, -27.9432, -27.8199,
         -28.0290, -42.6286, -27.9030,  38.0334]], grad_fn=<AddmmBackward0>)]
torch.Size([3, 128, 64])
torch.Size([1, 

torch.Size([3, 128, 64])
torch.Size([1, 3, 128, 64])
[tensor([[-15.7610,  -4.9811,  -8.9098, -11.3609, -13.1261, -13.0895,  -9.2848,
          -7.1074,  -8.5996, -10.2978, -47.8013]], grad_fn=<AddmmBackward0>), tensor([[ -5.4473,  -6.5894,  -8.1402, -10.0862, -11.4885, -11.8052, -11.6350,
          -6.4449,  -8.6207,  -7.3106,  -7.7695]], grad_fn=<AddmmBackward0>), tensor([[-14.5572, -13.5716, -15.5991, -16.8178, -15.7388, -17.5372, -16.4278,
         -13.2323, -14.9074, -16.9922, -13.3450]], grad_fn=<AddmmBackward0>), tensor([[-28.0653, -35.0392, -32.2378, -34.3388, -31.7725, -37.3536, -34.1642,
         -33.0870, -32.4476, -31.5961, -27.7466]], grad_fn=<AddmmBackward0>), tensor([[ -76.4368,  -99.1488,  -59.0275, -137.5012,  -58.9686, -103.2158,
          -58.9972,  -74.8592,  -58.8477,  -83.0976,  -24.8714]],
       grad_fn=<AddmmBackward0>), tensor([[-36.1346, -36.6778, -37.1180, -36.9198, -36.9696, -37.0789, -36.7516,
         -37.0318, -56.4859, -36.8833,  51.6834]], grad_fn=<Addm

torch.Size([3, 128, 64])
torch.Size([1, 3, 128, 64])
[tensor([[-13.2284,  -2.8512,  -8.1784,  -8.8447,  -8.2350,  -7.4837,  -5.7131,
          -8.4493,  -5.8886,  -8.4924, -40.0514]], grad_fn=<AddmmBackward0>), tensor([[-4.7210, -4.7127, -6.1166, -8.4313, -7.0043, -9.4315, -8.2081, -7.0121,
         -7.1017, -5.2540, -6.5629]], grad_fn=<AddmmBackward0>), tensor([[-11.9348, -10.8700, -12.0028, -13.5415, -10.9339, -12.7396, -13.7936,
         -12.4682, -12.9089, -11.5620, -10.1215]], grad_fn=<AddmmBackward0>), tensor([[-22.4849, -25.9797, -27.1439, -26.6701, -25.1068, -26.0224, -24.9212,
         -28.8120, -24.6591, -25.4610, -20.6029]], grad_fn=<AddmmBackward0>), tensor([[-60.8501, -56.2215, -51.4980, -80.0689, -51.5808, -83.2806, -51.5622,
         -59.5726, -51.6492, -73.6284, -25.9467]], grad_fn=<AddmmBackward0>), tensor([[-30.6475, -30.7778, -31.2323, -31.0187, -31.1104, -31.0793, -30.9934,
         -31.1923, -41.7519, -31.1034,  35.8451]], grad_fn=<AddmmBackward0>)]
torch.Size([3, 

C:\Users\62708\AppData\Local\Temp\ipykernel_9172\1633773713.py:40: FutureWarning: As the xlwt package is no longer maintained, the xlwt engine will be removed in a future version of pandas. This is the only engine in pandas that supports writing in the xls format. Install openpyxl and write to an xlsx file instead. You can set the option io.excel.xls.writer to 'xlwt' to silence this warning. While this option is deprecated and will also raise a warning, it can be globally set and the warning suppressed.
  df.to_excel("./predict.xls")


ModuleNotFoundError: No module named 'xlwt'

In [14]:
#Part2 测试image数据
import json
import numpy as np
import cv2
import matplotlib.pyplot as plt
train_json = json.load(open("./data/mchar_train.json"))

# 数据标注,切割处理
def parse_json(d):
    arr = np.array([
        d['top'], d['height'], d['left'],  d['width'], d['label']
    ])
    arr = arr.astype(int)
    return arr

img = cv2.imread('./data/mchar_train/mchar_train/000001.png')
img = cv2.cvtColor(img, cv2.COLOR_BGR2RGB) #Opencv默认颜色通道为BGR，需要转换
arr = parse_json(train_json['000001.png'])

plt.figure(figsize=(5, 1)) #figsize = (width,height)
plt.subplot(1, arr.shape[1]+1, 1) #subplot(行数，列数，位置)
plt.imshow(img)
plt.xticks([]); plt.yticks([]) #xticks()中填入数字，如[0，10，20，30]可以显示刻度

for idx in range(arr.shape[1]):
    plt.subplot(1, arr.shape[1]+1, idx+2)
    plt.imshow(img[arr[0, idx]:arr[0, idx]+arr[1, idx],arr[2, idx]:arr[2, idx]+arr[3, idx]]) #img[top:top+height,left:left+width] 
    plt.title(arr[4, idx])
    plt.xticks([]); plt.yticks([])